In [111]:
import pandas as pd
import numpy as np
import sys
sys.path.insert(1, '../')
from utils import *

In [112]:
data_dir = '../../datasets/lease_info'
site = 'uc'

In [113]:
df = pd.read_csv('%s/lease_info_%s.csv' % (data_dir, site))

Columns:
- Lease_id
- Project_id
- User_id
- Created_at: when the lease is created by the user
- Deleted_at: when the lease is deleted by the user (user may delete the lease before the scheduled lease expiration time)
- Start_on: when the lease starts
- End_on: when the lease ends (user may delete the lease before this time)
- Status: the final status of the lease (don’t trust this column. It may say “active”, but the lease is already terminated)
- Node_cnt: the number of nodes we give to the user
- Reserve_condition: what kind of nodes the user is asking for
- Reserve_count_range: the number of nodes the user is asking for (min-max)

In [114]:
df.shape

(30487, 11)

In [115]:
df.head(5)

lease_id                        project_id  \
0  c1568c33eec9d2a24aa97c868c2cf97b  6024816b7387ea63997c1c37abc3d338   
1  701d0083dc1199fc92309f55d5475210  a956639e292fd1679669a9507e4cd0c9   
2  83fb37cc0d211e4577597edb5f354652  eedcd4c64ea8cbbbf7b94258540171c2   
3  2e6619797ecfc077761a28f88c3e88ff  a956639e292fd1679669a9507e4cd0c9   
4  0674ff0b4b9eee6f5d0f13ab9643ab1f  a956639e292fd1679669a9507e4cd0c9   

                            user_id           created_at           deleted_at  \
0  a257de1fb61e44ae745ceb1467c3225e  2021-05-13 18:12:56  2021-05-24 17:29:26   
1  45b7d90a39ea685ec4fcba668a70cebd  2019-05-12 05:17:27  2019-05-12 05:31:30   
2  d271a59b4551cc100896c3a4550b7f43  2016-06-24 00:06:17  2016-06-28 00:42:08   
3  45b7d90a39ea685ec4fcba668a70cebd  2019-08-28 03:02:15  2019-08-28 03:03:13   
4  45b7d90a39ea685ec4fcba668a70cebd  2020-09-12 15:02:21  2020-09-12 15:03:19   

              start_on               end_on     status  node_cnt  \
0  2021-05-13 18:13:00  2021-05-20 18:12:00    deleted         1   
1  2019-05-12 05:18:00  2019-05-12 05:47:00     active         1   
2  2016-06-24 00:08:00  2016-06-30 00:08:00  completed         1   
3  2019-08-28 03:03:00  2019-08-28 04:03:00     active         1   
4  2020-09-12 15:03:00  2020-09-12 16:03:00     active         1   

                       reserve_conditions reserve_count_range  
0   ["==","$node_type","compute_haswell"]                 1-1  
1  ["=", "$node_type", "compute_skylake"]                 1-1  
2                                     NaN                 1-1  
3  ["=", "$node_type", "compute_haswell"]                 1-1  
4  ["=", "$node_type", "compute_haswell"]                 1-1

In [116]:
df['lease_id'].unique().shape

(30487,)

## Step 1. Select leases that were started successfully

In [117]:
df = df[~df['status'].isin(['pending', 'error', 'deleted'])]

## Step 2. Select leases that have specific node type requirements

In [118]:
from ast import literal_eval

# We assume users book lease based on node type only.
node_types = list(set([literal_eval(nt)[2] for nt in df['reserve_conditions'].dropna() if '$node_type' in literal_eval(nt)]))

In [119]:
import random
assign_nt = []
select_leases = []
for index, row in df.iterrows():
    if row['reserve_conditions'] is not np.nan:
        if '$node_type' in literal_eval(row['reserve_conditions']):
            assign_nt.append(literal_eval(row['reserve_conditions'])[2])
            select_leases.append(row['lease_id'])
    # else:
    #     # if the reserve_confition is NaN, assign a node type randomly
    #     assign_nt.append(node_types[random.randint(0, len(node_types)-1)])
    #     select_leases.append(row['lease_id'])

In [120]:
df = df[df['lease_id'].isin(select_leases)]
df['node_type'] = assign_nt
df.reset_index(drop=True, inplace=True)

In [121]:
df.groupby(by=['node_type']).count()['lease_id']

node_type
compute             1360
compute_haswell    14599
compute_skylake     2191
fpga                  21
gpu_rtx_6000         371
gpu_v100              24
storage              149
Name: lease_id, dtype: int64

In [122]:
df['reserve_conditions'].unique().shape

(19,)

## Step 3. Seperate on-deamd and in-advance requests

In [123]:
df.created_at = pd.to_datetime(df.created_at)
df.start_on = pd.to_datetime(df.start_on)
on_demand = df[(df.start_on - df.created_at) < '10M']
in_advance = df[(df.start_on - df.created_at) > '10M']

In [124]:
on_demand.shape

(18468, 12)

In [125]:
# most spikes are from the internal project
# to get more accurant on-demand user requests, 
# we exclude records belong to this project temporarily.
# internal_project_id = on_demand.groupby(by=['project_id'])['node_cnt'].sum().sort_values().index[-1]
# on_demand = on_demand[on_demand['project_id'] != internal_project_id]
# on_demand['node_cnt'].plot()

In [126]:
in_advance.shape

(247, 12)

## Step 4. Save data by node type and request type

In [127]:
import os

os.system('mkdir -p %s/on_demand/%s' % (data_dir, site))
os.system('mkdir -p %s/in_advance/%s' % (data_dir, site))

# save node types in seperate files
for nt in node_types:
    on_demand_nt = on_demand[on_demand['node_type'] == nt]
    on_demand_nt.sort_values(by=['start_on'], inplace=True)
    on_demand_nt.to_csv('%s/on_demand/%s/%s.csv' % (data_dir, site, nt), index=None)
    in_advance_nt = in_advance[in_advance['node_type'] == nt]
    in_advance_nt.sort_values(by=['start_on'], inplace=True)
    in_advance_nt.to_csv('%s/in_advance/%s/%s.csv' % (data_dir, site, nt), index=None)

ipykernel_launcher:9: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

ipykernel_launcher:12: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [128]:
from matplotlib.pylab import rcParams
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import seaborn as sns

def plot_lease(data):
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=data['start_on'], y=data['node_cnt'], mode='lines', name=nt))
    fig.update_layout(showlegend=True)
    fig.update_layout(
        margin=dict(l=20, r=20, t=20, b=20),
        paper_bgcolor="LightSteelBlue",
    )
    fig.show()

## TACC Data

In [129]:
import os
import pandas as pd
import numpy as np

In [130]:
nt = 'compute_haswell'
site = 'tacc'
df = pd.read_csv('%s/on_demand/%s/%s.csv' % (data_dir, site, nt))
df.sort_values(by=['start_on'], inplace=True)
plot_lease(df)
tacc_on_demand = df.copy()

In [131]:
df = pd.read_csv('%s/in_advance/%s/%s.csv' % (data_dir, site, nt))
df.sort_values(by=['start_on'], inplace=True)
plot_lease(df)
tacc_in_advance = df.copy()

## UC Data

In [132]:
import os
import pandas as pd
import numpy as np

In [133]:
nt = 'compute_haswell'
site = 'uc'

df = pd.read_csv('%s/on_demand/%s/%s.csv' % (data_dir, site, nt))
df.sort_values(by=['start_on'], inplace=True)
plot_lease(df)
uc_on_demand = df.copy()

In [134]:
df = pd.read_csv('%s/in_advance/%s/%s.csv' % (data_dir, site, nt))
df.sort_values(by=['start_on'], inplace=True)
plot_lease(df)
uc_in_advance = df.copy()

## Concat TACC and UC Data

In [135]:
df = pd.concat([tacc_on_demand, uc_on_demand, tacc_in_advance, uc_in_advance], axis=0)
df.sort_values(by=['start_on'], inplace=True)
df.to_csv('../../datasets/lease_info/%s.csv' % nt, index=None)

In [136]:
df

lease_id                        project_id  \
0      febb42dd11ff05674b55c3d57074dce3  a956639e292fd1679669a9507e4cd0c9   
1      03cc85360f61ad40149cab41a4645ecb  a956639e292fd1679669a9507e4cd0c9   
2      8748d9172666ee86e15ab83c38990512  a956639e292fd1679669a9507e4cd0c9   
0      ded3545b48463f8858b35d5c3e83e0cb  d79a64ad06b4569c01b79595b62207fb   
1      233eae66a6630015f2ddd11c4d34c45e  b519049daa0f6e72084b235ed0f6d8ed   
...                                 ...                               ...   
16192  a4f116661dd51012f2fd95b8a65133d2  f99d9532a5b5d343b83d24d66f222d74   
16193  41a2a5b877ca3cc1b4384ccb33929291  23a50d5b7f5a18599f2f5e4c75f1a883   
14555  c70448a99de00ac20640bdc92ebd011e  25c5e994513be7d408b390291b468c02   
16194  bf82659c6d1e5fd81bfa97f2fed47427  f24407401cb0b2fbae37abee8c3d8b7e   
16195  358c206f5c674c970827621a7a93dc65  f99d9532a5b5d343b83d24d66f222d74   

                                user_id           created_at  \
0      158b002b8fb423e2975fbe2f9d9f2c3a  2018-03-14 11:41:46   
1      45b7d90a39ea685ec4fcba668a70cebd  2018-03-14 12:05:27   
2      45b7d90a39ea685ec4fcba668a70cebd  2018-03-14 15:02:17   
0      99b54d1d4e70e31f2c092dcec7e5e3b8  2018-03-14 16:30:17   
1      b40f91fc9c93152f3fd696823e0f118d  2018-03-14 17:27:58   
...                                 ...                  ...   
16192  e50fbd600280ac3b0af27f91f0567cde  2021-06-07 17:41:13   
16193  64d7b8ae5a4754da22865b8092587e37  2021-06-07 17:59:34   
14555  69b69f18b9a80fed2064eb161abe708d  2021-06-07 19:26:45   
16194  bbc7d7bd1a27a96e8076b3f7f85ede4e  2021-06-07 19:34:10   
16195  202aad2123d2a56f8944dd56b5469599  2021-06-07 22:27:05   

                deleted_at             start_on               end_on  status  \
0      2018-03-14 16:43:00  2018-03-14 11:42:00  2018-03-15 11:41:00  active   
1      2018-03-14 12:06:23  2018-03-14 12:06:00  2018-03-14 13:06:00  active   
2      2018-03-14 15:03:13  2018-03-14 15:03:00  2018-03-14 16:03:00  active   
0      2018-03-14 16:31:21  2018-03-14 16:31:00  2018-03-14 17:31:00  active   
1      2018-03-14 17:31:13  2018-03-14 17:28:00  2018-03-15 17:27:00  active   
...                    ...                  ...                  ...     ...   
16192                  NaN  2021-06-07 17:42:00  2021-06-17 23:00:00  active   
16193  2021-06-08 00:02:49  2021-06-07 18:00:00  2021-06-14 17:59:00  active   
14555                  NaN  2021-06-07 19:26:00  2021-06-08 19:26:00  active   
16194                  NaN  2021-06-07 19:34:00  2021-06-08 19:34:00  active   
16195  2021-06-07 22:56:08  2021-06-07 22:27:00  2021-06-08 22:26:00  active   

       node_cnt                      reserve_conditions reserve_count_range  \
0             1   ["==","$node_type","compute_haswell"]                 1-1   
1             1  ["=", "$node_type", "compute_haswell"]                 1-1   
2             1  ["=", "$node_type", "compute_haswell"]                 1-1   
0             1  ["=", "$node_type", "compute_haswell"]                 1-1   
1             1   ["==","$node_type","compute_haswell"]                 1-1   
...         ...                                     ...                 ...   
16192         1   ["==","$node_type","compute_haswell"]                 1-1   
16193         1   ["==","$node_type","compute_haswell"]                 1-1   
14555         1  ["=", "$node_type", "compute_haswell"]                 1-1   
16194         1  ["=", "$node_type", "compute_haswell"]                 1-1   
16195         1   ["==","$node_type","compute_haswell"]                 1-1   

             node_type  
0      compute_haswell  
1      compute_haswell  
2      compute_haswell  
0      compute_haswell  
1      compute_haswell  
...                ...  
16192  compute_haswell  
16193  compute_haswell  
14555  compute_haswell  
16194  compute_haswell  
16195  compute_haswell  

[30931 rows x 12 columns]

In [137]:
plot_lease(df)